In [2]:
from itertools import chain
from nltk.corpus.reader import ConllCorpusReader

import nltk
import sklearn
import scipy.stats
from sklearn.metrics import make_scorer
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RandomizedSearchCV

import sklearn_crfsuite
from sklearn_crfsuite import scorers
from sklearn_crfsuite import metrics


In [1]:
%matplotlib inline
import matplotlib.pyplot as plt
plt.style.use('ggplot')


KeyboardInterrupt: 

In [ ]:
simbolos_pontuacao = ["'", '"', ",", ".", "!", ":", ";", '#', '@', '-']
texto = ['Lorem : "ipsum" \'dolor\', sit ! Amet ; bla ... bl @ #etc #, whiskas sache !!']

# incluí um elemento com mais de um caractere
simbolos_pontuacao = ['...', "'", '"', ",", "!", ":", ";", '#', '@']


import re

for c in simbolos_pontuacao:
    r = re.compile('({"|".join(map("\s+$", ""))})',texto)
#texto = r.sub('', texto)

print(r) # Lorem ipsum dolor sit Amet blabl etc whiskas sache


Let's use CoNLL 2003 data to build a NER system

We use English data.

Passo 1 - Treina o modelo

In [284]:
#conll2003
#with open('/home/82068895153/POS/skweak/data/conll2003_dataset/train.txt', 'r') as file:
with open('/Users/lucelia/POS/experimentos/Dataset/conll2003_dataset/train.txt', 'r') as file:

  sentences = list(file.readlines())

In [285]:
print (sentences[5])
len(sentences)

rejects VBZ B-VP O



219556

In [286]:
def preprocess(sentences):
    l_sentences = []
    l1_ = []
    for token in sentences[5:]: #a partir da quinta posicao
    #for token in sentences:
        #print('token==>', token)
        cls = token.split()    
        #print('token.split==>', cls)
        if len(cls) != 0:
            l1_.append(cls)
            #print('apos o append==>', l1_)
        else:
            l_sentences.append(l1_)
            l1_ = []
    return l_sentences

In [287]:
#Quebra a sentença em lista
sentences_1=preprocess(sentences)

In [288]:
print(sentences_1[5])

[['"', '"', 'O', 'O'], ['We', 'PRP', 'B-NP', 'O'], ['do', 'VBP', 'B-VP', 'O'], ["n't", 'RB', 'I-VP', 'O'], ['support', 'VB', 'I-VP', 'O'], ['any', 'DT', 'B-NP', 'O'], ['such', 'JJ', 'I-NP', 'O'], ['recommendation', 'NN', 'I-NP', 'O'], ['because', 'IN', 'B-SBAR', 'O'], ['we', 'PRP', 'B-NP', 'O'], ['do', 'VBP', 'B-VP', 'O'], ["n't", 'RB', 'I-VP', 'O'], ['see', 'VB', 'I-VP', 'O'], ['any', 'DT', 'B-NP', 'O'], ['grounds', 'NNS', 'I-NP', 'O'], ['for', 'IN', 'B-PP', 'O'], ['it', 'PRP', 'B-NP', 'O'], [',', ',', 'O', 'O'], ['"', '"', 'O', 'O'], ['the', 'DT', 'B-NP', 'O'], ['Commission', 'NNP', 'I-NP', 'B-ORG'], ["'s", 'POS', 'B-NP', 'O'], ['chief', 'JJ', 'I-NP', 'O'], ['spokesman', 'NN', 'I-NP', 'O'], ['Nikolaus', 'NNP', 'I-NP', 'B-PER'], ['van', 'NNP', 'I-NP', 'I-PER'], ['der', 'FW', 'I-NP', 'I-PER'], ['Pas', 'NNP', 'I-NP', 'I-PER'], ['told', 'VBD', 'B-VP', 'O'], ['a', 'DT', 'B-NP', 'O'], ['news', 'NN', 'I-NP', 'O'], ['briefing', 'NN', 'I-NP', 'O'], ['.', '.', 'O', 'O']]


In [289]:
def word2features(sent, i):
    
    word = sent[i][0]
    #print ('word', word)
    #postag = sent[i][1]
    #print ('postag', postag)

    features = {
        'bias': 1.0,
        'word.lower()': word.lower(),
        'word[-3:]': word[-3:],
        'word[-2:]': word[-2:],
        'word.isupper()': word.isupper(),
        'word.istitle()': word.istitle(),
        'word.isdigit()': word.isdigit(),
        #'postag': postag,
        #'postag[:2]': postag[:2],        
    }
    if i > 0:
        word1 = sent[i-1][0]
        #postag1 = sent[i-1][1]
        features.update({
            '-1:word.lower()': word1.lower(),
            '-1:word.istitle()': word1.istitle(),
            '-1:word.isupper()': word1.isupper(),
            #'-1:postag': postag1,
            #'-1:postag[:2]': postag1[:2],
        })
    else:
        features['BOS'] = True
        
    if i < len(sent)-1:
        word1 = sent[i+1][0]
        #postag1 = sent[i+1][1]        
        features.update({
            '+1:word.lower()': word1.lower(),
            '+1:word.istitle()': word1.istitle(),
            '+1:word.isupper()': word1.isupper(),
            #'+1:postag': postag1,
            #'+1:postag[:2]': postag1[:2],
        })
    else:
        features['EOS'] = True
                
    return features


In [290]:
def sent2features(sent):
    return [word2features(sent, i) for i in range(len(sent))]

def sent2labels(sent):
    return [label for token, postag, __, label in sent]

def sent2tokens(sent):
    return [token for token, postag, __, label in sent]


In [291]:
X_train = [sent2features(s) for s in sentences_1]

y_train = [sent2labels(s) for s in sentences_1]


In [292]:
X_train[1]

[{'bias': 1.0,
  'word.lower()': 'peter',
  'word[-3:]': 'ter',
  'word[-2:]': 'er',
  'word.isupper()': False,
  'word.istitle()': True,
  'word.isdigit()': False,
  'BOS': True,
  '+1:word.lower()': 'blackburn',
  '+1:word.istitle()': True,
  '+1:word.isupper()': False},
 {'bias': 1.0,
  'word.lower()': 'blackburn',
  'word[-3:]': 'urn',
  'word[-2:]': 'rn',
  'word.isupper()': False,
  'word.istitle()': True,
  'word.isdigit()': False,
  '-1:word.lower()': 'peter',
  '-1:word.istitle()': True,
  '-1:word.isupper()': False,
  'EOS': True}]

In [293]:
y_train[1] 

['B-PER', 'I-PER']

In [295]:
import sklearn_crfsuite

crf = sklearn_crfsuite.CRF(
    algorithm='lbfgs', 
    c1=0.5, 
    c2=1e-3, 
    max_iterations=100, 
    all_possible_transitions=True,
    #verbose=True
)

#CRF(algorithm='lbfgs', all_possible_states=None, all_possible_transitions=True,
#    averaging=None, c=None, c1=0.1, c2=0.1, calibration_candidates=None,
#    calibration_eta=None, calibration_max_trials=None, calibration_rate=None,
#    calibration_samples=None, delta=None, epsilon=None, error_sensitive=None,
#    gamma=None, keep_tempfiles=None, linesearch=None, max_iterations=100,
#    max_linesearch=None, min_freq=None, model_filename=None, num_memories=None,
#    pa_type=None, period=None, trainer_cls=None, variance=None, verbose=True)

In [296]:
crf.fit(X_train, y_train)

CRF(algorithm='lbfgs', all_possible_transitions=True, c1=0.5, c2=0.001,
    keep_tempfiles=None, max_iterations=100)

Passo 2 - Prepara o Y_test a partir do dataset do Ontonotes 

In [11]:
#2.1 - Abre o Ontonotes para aplicar o tratamento 
#with open('/home/82068895153/POS/skweak/data/Ontonotes/ner_train.txt', 'r') as file:
with open('/Users/lucelia/POS/experimentos/Dataset/Ontonotes/ner_train.txt', 'r') as file:
#dataset com 1000 linhas para teste
#with open('/Users/lucelia/POS/experimentos/Dataset/Ontonotes/ner_train_lu.txt', 'r') as file:
   sentences = list(file.readlines())

In [12]:
len(sentences) 

517630

In [13]:
#2.2 - Retira os espaços em branco e as words maiores que duas posições
for i in range(len(sentences) - 1):
    #print(sentences[116:122])
    atual = sentences[i].split()
    proximo = sentences[i+1].split()
    if len(atual) == 0:
        continue
    while len(proximo) > 2:
        #print(f'Convertendo ({atual}) e ({proximo}) para ', end = '')
        atual[0] += proximo[0]
        sentences[i] = '\t'.join(atual)+'\n'
        proximo = proximo[1:]
        sentences[i+1] = '\t'.join(proximo)+'\n'
        #print(f'({atual}) e ({proximo})')

In [14]:
len(sentences)

517630

In [15]:
#2.3 - Verifica as linhas com mais de duas words e concatena
for i in range(len(sentences) - 1):
        atual = sentences[i].split()
        if ((len(atual)>2) and (len(atual)<=3)):
            #print('atual', atual)
            sentences[i]=(''.join(atual[0]+atual[1]))+' '+atual[2]+'\n' 
            #print('sentences', sentences[i])
            #print(i)
        elif ((len(atual)>3) and (len(atual)<=4)):
            #print('atual', atual)
            sentences[i]=(''.join(atual[0]+atual[1]+atual[2]))+' '+atual[3] +'\n'  
            #print('sentences', sentences[i])
            #print(i)
        elif (len(atual)>4):
            sentences[i]=(''.join(atual[0]+atual[1]+atual[2]+atual[3]))+' '+atual[4] +'\n' 
            #print(i)

In [16]:
with open('/Users/lucelia/POS/experimentos/Dataset/Ontonotes/ner_train_limpo.txt', 'wt') as fileout:
    fileout.writelines(sentences)

In [53]:
print(sentences[121:150])

[]


In [121]:
len(sentences)

3160787

In [6]:
#2.4 - carrega a função para detecção da língua
import spacy
from spacy.language import Language
from spacy_langdetect import LanguageDetector
#na primeira execução descomentar essa linha
@Language.factory("language_detector")
def get_lang_detector(nlp, name):
   return LanguageDetector()

nlp = spacy.load("en_core_web_sm")
nlp.add_pipe('language_detector', last=True)
#print(nlp('场')._.language)

In [9]:
#2.5 - cria a função que detecta linha a linha a língua e remove tudo que não for Inglês
#Remove a linha apenas ocasionando eliminações indevidas
""" def limpaOntonotes(linhas):
    #count=0
    lista = []
    for line in linhas:
        line1=line.split('\t')
        if len(line1)>1:
            result = nlp(line1[0])
            #print(line1[0])
            #print(line1[1])
            result1 = nlp(line1[1])
        
            #print(result)
            if((result._.language) or (result1._.language)):
                #print(result._.language)
                result=(result._.language['language'])
                result1=(result1._.language['language'])
                #print('line', line)
                #print('result', result)
                if (result or result1) not in ['ko','zh-cn','ar','fa','zh-tw','fa', 'es','sw','id']:
                #if result not in lang:
                    #print('lista', lista) 
                    lista.append(line)
                    #print(lista)
        if (len(line1)==1):
            #print('entrou no if')
            lista.append('\n')
        #count+=1
        #print(count)    
    return lista  
 """

In [ ]:
#lang = ['af' , 'ar' , 'bg' , 'bn' , 'ca' , 'cs' , 'cy' , 'da' , 'de' , 'el' , 'es' , 'et' , 'fa' , 'fi' , 'fr' , 'gu' , 'he' , 'hi' , 'hr' , 'hu' , 'id' , 'it' , 'ja' , 'kn' , 'ko' , 'lt' , 'lv' , 'mk' , 'ml' , 'mr' , 'ne' , 'nl' , 'no' , 'pa' , 'pl' , 'pt' , 'ro' , 'ru' , 'sk' , 'sl' , ' sq' , 'sv' , 'sw' , 'ta' , 'te' , 'th' , 'tl' , 'tr' , 'uk' , 'ur' , 'vi' , 'zh-cn' , 'zh-tw']
#lang = ['ar', 'fa', 'es' ,'id',  'ko' , 'sw' , 'zh-cn', 'zh-tw']
#['af'  , 'bg' , 'bn' , 'ca' , 'cs' , 'cy' , 'da' , 'de' , 'el', 'et' , 'fi' , 'fr' , 'gu' , 'he' , 'hi' , 'hr' , 'hu' , 'it' , 'ja' , 'kn' , 'lt' , 'lv' , 'mk' , 'ml' , 'mr' , 'ne' , 'nl' , 'no' , 'pa' , 'pl' , 'pt' , 'ro' , 'ru' , 'sk' , 'sl' , ' sq' , 'sv' , 'ta' , 'te' , 'th' , 'tl' , 'tr' , 'uk' , 'ur' , 'vi']

In [ ]:
#lista = limpaOntonotes(['مسيرت','并不','高子平','告诉','记者','这些','收入','对','مريم','العذراء','预报','uh-huh','Good', 'school'])
#lista_1 = limpaOntonotes(['他','还','强调','现在'])
#lista_1 = limpaOntonotes(['他','还','强调','，','这些','并不','意味','着','将','有','一','场','战争'])

#2.6 Chama a função de detecção da língua
#lista_1=limpaOntonotes(sentences)

In [124]:
#2.5 - cria a função que detecta dentro da sentenca a língua e remove toda a sentenca se alguma palavra não for Inglês
#encoding: utf-8
#txt = ['A\tO\n', 'House\tO\n', '.\tO\n', '\n', 'Pedro\tPER\n', '.\tO\n', '\n', 'Doing\tVERB\n', 'something\tO\n', '\n']

def list_of_lists_to_list_of_strings(ls):
    return [' '.join(l) for l in ls]

def lines_to_sentences(lines):
    """
    Só funciona se último elemento de lines for '\n',
    se não for assim no seu caso adicione um no final
    caso contrário vai pular a última sentença
    """
    sentences = []
    labels = []
    sentence = []
    label = []
    for line in lines:
        if line == '\n':
            sentences.append(sentence)
            labels.append(label)
            sentence = []
            label = []
            print('entrou no for --> sentences, labels', sentences, labels)
        else:
            word, word_label = line.strip('\n').split('\t')
            sentence.append(word)
            label.append(word_label)
    
    sentences = list_of_lists_to_list_of_strings(sentences)
    labels = list_of_lists_to_list_of_strings(labels)
    return sentences, labels

#print('Sentenças e labels separados')
sentences, labels = lines_to_sentences(txt)
#print(sentences)
#print(labels)

# class LanguageDetector:
#     """Alterna a linguagem detectada só pra teste"""
#     def __init__(self):
#         self.l = True

#     def lang(self, sentence):
#         if self.l:
#             language = 'en'
            
#         else:
#             language = 'ko'
#         self.l = not self.l
#         return language

ValueError: not enough values to unpack (expected 2, got 1)

In [ ]:
#USEI ESTE
def filter_sentences(sentences, labels):
    """
    filtra pela linguagem
    """
    filtered_sentences = []
    filtered_labels = []
    #ld = LanguageDetector()

    for sentence, label in zip(sentences, labels):
        #if ld.lang(sentence) == 'en':
        result = nlp(sentence)
        
        if result._.language['language'] == 'en':
            print('sentenca', sentence, 'label',label, 'result',  result._.language['language'])
            filtered_sentences.append(sentence)
            filtered_labels.append(label)
        
    return filtered_sentences, filtered_labels


In [ ]:
def sentences_to_lines(sentences, sentence_labels):
    """
    Contrário de lines_to_sentences
    """
    lines = []
    for sentence, labels in zip(sentences, sentence_labels):
        words = sentence.split(' ')
        word_labels = labels.split(' ')
        for word, label in zip(words, word_labels):
            # line = f'{word}\t{label}\n'
            line = word + '\t' + label + '\n'
            lines.append(line)
        lines.append('\n')
    return lines

In [ ]:
#print('Sentenças e labels filtrados pela linguagem')
filtered_sentences, filtered_labels = filter_sentences(sentences, labels)
#print(filtered_sentences)
#print(filtered_labels)

In [ ]:
#print('Linhas após filtragem')
filtered_lines = sentences_to_lines(filtered_sentences, filtered_labels)
#print(filtered_lines)

In [ ]:
# Outra fução para detecçõ da lingua, usei a anterior. 

#detect("War doesn't show who's right, just who's left.")

def limpaOntonotes_1(linhas):
    from langdetect import detect
    lista = []
    for line in linhas[0:500]:
# the try except blook because there is some tweets contain links
        if not line: #verifica se a linha está vazia
            #print('line', line)
            result = detect(line)
            #print(result)
            if result not in lang:
                #print('lista', lista)
                lista.append(line)
            #print(lista)
        else:
            lista.append(line)
    return lista  


In [ ]:
#limpaOntonotes(['他','还','强调','现在','Good Morning'])
#lista_1=limpaOntonotes_1(sentences)

In [106]:
#gravação de teste
#with open('/Users/lucelia/POS/experimentos/Dataset/Ontonotes/ner_train_lista.txt', 'wt') as fileout:
#    fileout.writelines(lista_1)

#with open('/home/82068895153/POS/skweak/data/Ontonotes/ner_train_setences.txt', 'wt') as fileout:
#
#Grava arquivo após retirada de linguas não inglesas
#     
with open('/Users/lucelia/POS/experimentos/Dataset/Ontonotes/ner_train_limpo_1.txt', 'wt') as fileout:
    fileout.writelines(filtered_lines)

In [17]:
#
#Abre arquivo após retirada de linguas não inglesas
#     

#with open('/home/82068895153/POS/skweak/data/Ontonotes/ner_train_setences.txt', 'r') as file:
with open('/Users/lucelia/POS/experimentos/Dataset/Ontonotes/ner_train_limpo_1.txt', 'r') as file:
    sentences_trat = file.readlines()

In [18]:
len(sentences_trat)

2051762

In [14]:
#
# Função de troca dos labels padrão conll2003
#     

def troca(linhas, termo, termo_cabeca, termo_corpo):
    newlines = []
    is_in_body = False
    for line in linhas:
        if termo in line:
            if not is_in_body:
                #retira \n e insere termo depois
                word = line.split()
                newLine = word[0] + ' ' + termo_cabeca + '\n' 
                #print('PRIMEIRA OCORRENCIA')
                #print('line',line)
                #print('newLine',newLine)
            else:
                word = line.split()
                newLine = word[0] + ' ' + termo_corpo + '\n'
                #print('SEGUNDA OCORRENCIA')
                #print('line',line)
                #print('newLine',newLine)
            is_in_body = True
        else:
            is_in_body = False
            newLine = line
        newlines.append(newLine)
    return newlines


In [19]:
#
# Troca dos labels padrão conll2003
# 
lines = troca(sentences_trat, 'GPE', 'B-LOC', 'I-LOC')
lines1 = troca(lines, 'PERSON', 'B-PER', 'I-PER')
lines2 = troca(lines1, 'ORG', 'B-ORG', 'I-ORG')
lines3 = troca(lines2, 'LOC', 'B-LOC', 'I-LOC')
lines4 = troca(lines3, 'PERCENT', 'B-MISC','I-MISC')
lines5 = troca(lines4, 'FAC', 'B-MISC','I-MISC')
lines6 = troca(lines5, 'CARDINAL', 'B-MISC','I-MISC') 
lines7 = troca(lines6, 'QUANTITY', 'B-MISC','I-MISC') 
lines8 = troca(lines7, 'DATE', 'B-MISC','I-MISC') 
lines9 = troca(lines8, 'EVENT', 'B-MISC','I-MISC') 
lines10 = troca(lines9, 'MONEY', 'B-MISC','I-MISC') 
lines11 = troca(lines10, 'NORP', 'B-MISC','I-MISC') 
lines12 = troca(lines11, 'PRODUCT', 'B-MISC','I-MISC') 
lines13 = troca(lines12, 'TIME', 'B-MISC','I-MISC') 
lines14 = troca(lines13, 'FAC', 'B-MISC','I-MISC') 
lines15 = troca(lines14, 'LAW', 'B-MISC','I-MISC') 

In [20]:
#
# Grava o Ontonotes após aplicar ajuste do label
# 

#with open('/home/82068895153/POS/skweak/data/Ontonotes/ner_train_label.txt', 'wt') as fileout:
with open('/Users/lucelia/POS/experimentos/Dataset/Ontonotes/ner_train_label.txt', 'wt') as fileout:
    fileout.writelines(lines15)

In [217]:
#
# Abre o Ontonotes após aplicar ajuste do label
#
#with open('/home/82068895153/POS/skweak/data/Ontonotes/ner_train_label.txt', 'r') as file:
with open('/Users/lucelia/POS/experimentos/Dataset/Ontonotes/ner_train_label_teste_01_ajuste.txt', 'r') as file:
   sentences_trat_label = list(file.readlines())

In [166]:
len(sentences_trat_label)

517590

In [167]:
print(sentences_trat_label[0:70])

['You\tO\n', 'know\tO\n', 'what\tO\n', '?\tO\n', '\n', 'The\tO\n', 'school\tO\n', 'is\tO\n', 'going\tO\n', 'to\tO\n', 'be\tO\n', 'closed\tO\n', 'for\tO\n', 'the O\n', 'rest O\n', 'of O\n', 'the O\n', 'week O\n', 'Anderson B-PER\n', '.\tO\n', '\n', 'Well\tO\n', ',\tO\n', 'actually\tO\n', ',\tO\n', 'regarding\tO\n', ',\tO\n', 'um\tO\n', ',\tO\n', "Koizumi's B-PER\n", 'attendance\tO\n', 'at\tO\n', 'this\tO\n', 'APEC B-ORG\n', 'summit\tO\n', ',\tO\n', 'people\tO\n', 'are\tO\n', 'more\tO\n', 'interested\tO\n', 'in\tO\n', 'the\tO\n', 'relations\tO\n', 'between\tO\n', 'Japan B-LOC\n', 'and\tO\n', 'its\tO\n', 'Asian B-LOC\n', 'neighboring\tO\n', 'countries\tO\n', ',\tO\n', 'including\tO\n', 'the\tO\n', 'kind\tO\n', 'of\tO\n', 'alliance\tO\n', 'relationship\tO\n', 'between\tO\n', 'the\tO\n', 'US B-LOC\n', 'and\tO\n', 'Japan B-LOC\n', ',\tO\n', 'and\tO\n', 'so\tO\n', 'on\tO\n', '.\tO\n', '\n', 'I\tO\n', 'bought\tO\n']


In [ ]:
#2.6 - Insere linha entre as sentenças
""" arq1 = ''
for linha in lines15:

#for linha in sentences_trat:
    p=linha.find('.')
    #print('linha', linha)
    #print ('p == ',p)
    if p==0:
        arq1=arq1+linha+'\n'
        #print ('arq de p0 == ',arq)
    else:
        arq1=arq1+linha
        #print ('arq de p = . == ',arq) """

In [ ]:
#2.7 - Grava o arquivo após o tratamento
#with open('/home/82068895153/POS/skweak/data/Ontonotes/ner_train_arq1.txt', 'wt') as fileout:
#    fileout.writelines(sentences_trat_label)

In [ ]:
#2.7 - Abre o Ontonotes após concluir o tratamento para carregar o y_test
#with open('/home/82068895153/POS/skweak/data/Ontonotes/ner_train_arq1.txt', 'r') as file:
#   arq_sentences = list(file.readlines())

In [297]:
#2.8 - cria a função para inserir tokens dentro das sentencas -- quebra a setenca em uma lista
def preprocess_b(arq_sentences):
    l_sentences = []
    l1_ = []
    for token in arq_sentences[0:]: #a partir da quinta posicao
    #for token in sentences:
        #print('token==>', token)
        cls = token.split()    
        #print('token.split==>', cls)
        if len(cls) != 0:
            l1_.append(cls)
            #print('apos o append==>', l1_)
        else:
            l_sentences.append(l1_)
            l1_ = []
    return l_sentences

In [298]:
#2.9  Aplica a função de tokens ao arquivo aberto
arq_sentences_1 = preprocess_b(sentences_trat_label)

In [299]:
print(arq_sentences_1[0:16])

[[['You', 'O'], ['know', 'O'], ['what', 'O'], ['?', 'O']], [['The', 'O'], ['school', 'O'], ['is', 'O'], ['going', 'O'], ['to', 'O'], ['be', 'O'], ['closed', 'O'], ['for', 'O'], ['the', 'O'], ['rest', 'O'], ['of', 'O'], ['the', 'O'], ['week', 'O'], ['Anderson', 'B-PER'], ['.', 'O']], [['Well', 'O'], [',', 'O'], ['actually', 'O'], [',', 'O'], ['regarding', 'O'], [',', 'O'], ['um', 'O'], [',', 'O'], ["Koizumi's", 'B-PER'], ['attendance', 'O'], ['at', 'O'], ['this', 'O'], ['APEC', 'B-ORG'], ['summit', 'O'], [',', 'O'], ['people', 'O'], ['are', 'O'], ['more', 'O'], ['interested', 'O'], ['in', 'O'], ['the', 'O'], ['relations', 'O'], ['between', 'O'], ['Japan', 'B-LOC'], ['and', 'O'], ['its', 'O'], ['Asian', 'B-LOC'], ['neighboring', 'O'], ['countries', 'O'], [',', 'O'], ['including', 'O'], ['the', 'O'], ['kind', 'O'], ['of', 'O'], ['alliance', 'O'], ['relationship', 'O'], ['between', 'O'], ['the', 'O'], ['US', 'B-LOC'], ['and', 'O'], ['Japan', 'B-LOC'], [',', 'O'], ['and', 'O'], ['so', 'O'],

In [300]:
len(arq_sentences_1)

25067

In [301]:
#
# Função para extrair os rotulos reais
#
def sent2labelsO(sent):
    return [label for token, label in sent]


In [302]:
#
#  Verifica se o dataset tem mais elementos que a chamado do métoddo sent2labels
#
for sentences in arq_sentences_1:
    #print(sentences) 
    try: 
        _ = sent2labelsO(sentences)
      
    except ValueError:
        print(sentences) 
        for word in sentences:
            
            if len(word)!= 2:
                print(f' {word} possui {len(word)} elementos.')
                
                 
        break

In [303]:
#3.2 Extrai os rótulos reais y_test
y_test = [sent2labelsO(sentences) for sentences in arq_sentences_1]   

In [172]:
y_test

[['O', 'O', 'O', 'O'],
 ['O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'B-PER',
  'O'],
 ['O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'B-PER',
  'O',
  'O',
  'O',
  'B-ORG',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'B-LOC',
  'O',
  'O',
  'B-LOC',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'B-LOC',
  'O',
  'B-LOC',
  'O',
  'O',
  'O',
  'O',
  'O'],
 ['O', 'O', 'O', 'O', 'O', 'O'],
 ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O'],
 ['O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O'],
 ['O',
  'O',
  'O',
  'B-ORG',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O'],
 ['O',
  'O',
  'O',
  'B-ORG',
  'I-ORG',
  'I-ORG',
  'I-ORG',
  'O',
  'O'

In [304]:
len(y_test)

25067

Passo 3 - Carrega o X_test a partir do dataset do Ontonotes 

In [305]:
#2.1 - Abre o Ontonotes para aplicar o tratamento 
#with open('/home/82068895153/POS/skweak/data/Ontonotes/ner_train.txt', 'r') as file:
with open('/Users/lucelia/POS/experimentos/Dataset/Ontonotes/ner_train_label_teste_01_ajuste.txt', 'r') as file:
   sentences_x = list(file.readlines())

In [306]:
#2.2 - Remove o label original
def removeLabel(linhas):
    #novoTexto = []
    newLines=[]
    for line in linhas: 
        if len(line)!=1:
            word = line.split()
            newLine = word[0]+ '\n'
            #print('entrou no if')
            #print(newLine)
            
        else:
            newLine = line 
            #print('entrou no else')
        newLines.append(newLine)
        #print(newLines)
    return newLines       

In [307]:
texto_sem_label = removeLabel(sentences_x)

In [308]:
print(texto_sem_label[0:100])

['You\n', 'know\n', 'what\n', '?\n', '\n', 'The\n', 'school\n', 'is\n', 'going\n', 'to\n', 'be\n', 'closed\n', 'for\n', 'the\n', 'rest\n', 'of\n', 'the\n', 'week\n', 'Anderson\n', '.\n', '\n', 'Well\n', ',\n', 'actually\n', ',\n', 'regarding\n', ',\n', 'um\n', ',\n', "Koizumi's\n", 'attendance\n', 'at\n', 'this\n', 'APEC\n', 'summit\n', ',\n', 'people\n', 'are\n', 'more\n', 'interested\n', 'in\n', 'the\n', 'relations\n', 'between\n', 'Japan\n', 'and\n', 'its\n', 'Asian\n', 'neighboring\n', 'countries\n', ',\n', 'including\n', 'the\n', 'kind\n', 'of\n', 'alliance\n', 'relationship\n', 'between\n', 'the\n', 'US\n', 'and\n', 'Japan\n', ',\n', 'and\n', 'so\n', 'on\n', '.\n', '\n', 'I\n', 'bought\n', 'one\n', 'of\n', 'his\n', 'arrangements\n', '\n', 'We\n', 'wo\n', "n't\n", 'do\n', 'photo\n', 'red\n', ',\n', 'and\n', 'you\n', 'are\n', 'suggesting\n', 'this\n', '?\n', '\n', 'He\n', 'does\n', "n't\n", 'seem\n', 'to\n', 'be\n', 'backing\n', 'away\n', 'from\n', 'those\n', 'controversial\n']


In [309]:
len(texto_sem_label)

517590

In [310]:
#2.3 - Grava o arquivo após o tratamento
#with open('/home/82068895153/POS/skweak/data/Ontonotes/ner_train_sem_label.txt', 'wt') as fileout:
with open('/Users/lucelia/POS/experimentos/Dataset/Ontonotes/ner_train_sem_label_teste_01_ajuste.txt', 'wt') as fileout:
    fileout.writelines(texto_sem_label)

In [311]:
#2.4 - Abre o Ontonotes após concluir o tratamento para carregar o X_text
#with open('/home/82068895153/POS/skweak/data/Ontonotes/ner_train_sem_label.txt', 'r') as file:
with open('/Users/lucelia/POS/experimentos/Dataset/Ontonotes/ner_train_sem_label_teste_01_ajuste.txt', 'r') as file:
   texto_sem_label_1 = list(file.readlines())

In [312]:
len(texto_sem_label_1)

517590

In [313]:
#2.5 - Cria os tokens dentro das sentencas -- quebra a setenca em uma lista
def preprocess_O(arq_sentences):
    l_sentences = []
    l1_ = []
    for token in arq_sentences[0:]: #a partir da quinta posicao
    #for token in sentences:
        #print('token==>', token)
        cls = token.split()    
        #print('token.split==>', cls)
        if len(cls) != 0:
            l1_.append(cls)
            #print('apos o append==>', l1_)
        else:
            l_sentences.append(l1_)
            l1_ = []
    return l_sentences

In [319]:
#2.9 - Transforma a sentença em lista
test_sentences_2=preprocess_O(texto_sem_label_1)

In [315]:
print(test_sentences_2)

[[['You'], ['know'], ['what'], ['?']], [['The'], ['school'], ['is'], ['going'], ['to'], ['be'], ['closed'], ['for'], ['the'], ['rest'], ['of'], ['the'], ['week'], ['Anderson'], ['.']], [['Well'], [','], ['actually'], [','], ['regarding'], [','], ['um'], [','], ["Koizumi's"], ['attendance'], ['at'], ['this'], ['APEC'], ['summit'], [','], ['people'], ['are'], ['more'], ['interested'], ['in'], ['the'], ['relations'], ['between'], ['Japan'], ['and'], ['its'], ['Asian'], ['neighboring'], ['countries'], [','], ['including'], ['the'], ['kind'], ['of'], ['alliance'], ['relationship'], ['between'], ['the'], ['US'], ['and'], ['Japan'], [','], ['and'], ['so'], ['on'], ['.']], [['I'], ['bought'], ['one'], ['of'], ['his'], ['arrangements']], [['We'], ['wo'], ["n't"], ['do'], ['photo'], ['red'], [','], ['and'], ['you'], ['are'], ['suggesting'], ['this'], ['?']], [['He'], ['does'], ["n't"], ['seem'], ['to'], ['be'], ['backing'], ['away'], ['from'], ['those'], ['controversial'], ['comments'], ['the'],

In [316]:
len(test_sentences_2)

25067

In [317]:
#3.0 - Função para extrair as features do texto a ser rotulado

def word2featuresO(sent, i):
    #word = sent[i][0]
    word = sent[i]
    features = {
        'bias': 1.0,
        'word.lower()': word.lower(),
        'word[-3:]': word[-3:],
        'word[-2:]': word[-2:],
        'word.isupper()': word.isupper(),
        'word.istitle()': word.istitle(),
        'word.isdigit()': word.isdigit()  
    }
    if i > 0:
        word1 = sent[i-1]
        features.update({
            '-1:word.lower()': word1.lower(),
            '-1:word.istitle()': word1.istitle(),
            '-1:word.isupper()': word1.isupper()
        })
    else:
        features['BOS'] = True
        
    if i < len(sent)-1:
        word1 = sent[i+1]       
        features.update({
            '+1:word.lower()': word1.lower(),
            '+1:word.istitle()': word1.istitle(),
            '+1:word.isupper()': word1.isupper()
        })
    else:
        features['EOS'] = True
                
    return features

In [320]:
#3.1 - Função para chamada da Função para extrair as features do texto a ser rotulado
def sent2featuresO(sent):
    return [word2featuresO(sent, i) for i in range(len(sent))]

In [321]:
#
# Extrai as fetatures de X_test
#  
X_test = [[sent2featuresO(s) for s in text] for text in test_sentences_2]

In [40]:
len(X_test)

25067

In [43]:
X_test[0]

[[{'bias': 1.0,
   'word.lower()': 'you',
   'word[-3:]': 'You',
   'word[-2:]': 'ou',
   'word.isupper()': False,
   'word.istitle()': True,
   'word.isdigit()': False,
   'BOS': True,
   'EOS': True}],
 [{'bias': 1.0,
   'word.lower()': 'know',
   'word[-3:]': 'now',
   'word[-2:]': 'ow',
   'word.isupper()': False,
   'word.istitle()': False,
   'word.isdigit()': False,
   'BOS': True,
   'EOS': True}],
 [{'bias': 1.0,
   'word.lower()': 'what',
   'word[-3:]': 'hat',
   'word[-2:]': 'at',
   'word.isupper()': False,
   'word.istitle()': False,
   'word.isdigit()': False,
   'BOS': True,
   'EOS': True}],
 [{'bias': 1.0,
   'word.lower()': '?',
   'word[-3:]': '?',
   'word[-2:]': '?',
   'word.isupper()': False,
   'word.istitle()': False,
   'word.isdigit()': False,
   'BOS': True,
   'EOS': True}]]

In [322]:
#3.2 - Retira o X_teste de dentro da lista aninhada para execução do y_pred
#
for i in range(len(X_test)):
        X_test[i] = [i[0] for i in X_test[i]]

4 - Passo: Gerar o y_pred = rotulos preditos para o texto não rotulado

In [323]:
#
# Aplica o modelo treinado no dataset sem rotulos
#
y_pred = crf.predict(X_test)


In [324]:
y_pred

[['O', 'O', 'O', 'O'],
 ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O'],
 ['O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'B-LOC',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'B-LOC',
  'O',
  'O',
  'O',
  'O',
  'O'],
 ['O', 'O', 'O', 'O', 'O', 'O'],
 ['O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O'],
 ['O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O'],
 ['O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O'],
 ['O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O',
  'O'],
 ['O',
  

In [325]:
len(y_pred)

25067

In [44]:
#Checa se as word do Y_test com o Y_pred estão batendo
 #len(sentences_trat) , len(arq_sentences_2) 
 
for i in range(len(arq_sentences_1)):
    predicao = arq_sentences_1[i].split()
    real =  sentences_trat[i].split()
    #print('predicao',predicao[0] )
    #print('real', real[0])
    if predicao[0] != real[0]:
        print(i)
        print('real', real, i)
        print('predicao', predicao, i)

AttributeError: 'list' object has no attribute 'split'

In [46]:
#teste= zip(test_sentences_2[0:1], y_pred[500:501])

lista=[]

for sentence, label_lista in zip(test_sentences_2, y_pred):
            # line = f'{word}\t{label}\n'
            #print(word[0][0])
            #print(label[0])
        for word, label in zip(sentence, label_lista):
            line = word + '\t' + label + '\n'
            lista.append(line)
        lista.append('\n')
#print ('predicao', lista)
#print ('real' ,  arq_sentences_1[500:520])



In [50]:
with open('/Users/lucelia/POS/experimentos/Dataset/Ontonotes/ner_train_final.txt', 'wt') as fileout:
    fileout.writelines(lista)

In [198]:
print('word do y_test   ==>', arq_sentences_1[14],'\n')
print('word do y_pred   ==>', test_sentences_2[14],'\n')
print('label do y_test  ==>',y_test[15],'\n')
print('label do y_pred  ==>',y_pred[15],'\n')

word do y_test   ==> [['The', 'O'], ['number', 'O'], ['of', 'O'], ['experimental', 'O'], ['cities', 'O'], ['involved', 'O'], ['in', 'O'], ['optimizing', 'O'], ['capital', 'O'], ['structure', 'O'], ['increased', 'O'], ['from', 'O'], ['58', 'O'], ['to', 'O'], ['111', 'O'], [';', 'O'], ['key', 'O'], ['enterprises', 'O'], ['on', 'O'], ['which', 'O'], ['the', 'O'], ['state', 'O'], ['placed', 'O'], ['extra', 'O'], ['emphasis', 'O'], ['increased', 'O'], ['from', 'O'], ['300', 'O'], ['to', 'O'], ['512', 'O'], ['and', 'O'], ['experimental', 'O'], ['surveys', 'O'], ['of', 'O'], ['the', 'O'], ['enterprise', 'O'], ['group', 'O'], ['increased', 'O'], ['from', 'O'], ['57', 'O'], ['to', 'O'], ['120', 'O'], ['.', 'O']] 

word do y_pred   ==> [['The'], ['number'], ['of'], ['experimental'], ['cities'], ['involved'], ['in'], ['optimizing'], ['capital'], ['structure'], ['increased'], ['from'], ['58'], ['to'], ['111'], [';'], ['key'], ['enterprises'], ['on'], ['which'], ['the'], ['state'], ['placed'], ['ex

In [146]:
count = 0
for i,x in enumerate(y_pred):
        ss=set(x)
        if len(ss) > 1:
            count+=1
print("Qtde labels preditos", count)
print("Qtde de tokens ", )
#print("tamanho y_pred", len(y_pred))

Qtde labels preditos 1134
Qtde de tokens 


Avaliação

There is much more O entities in data set, but we’re more interested in other entities. To account for this we’ll use averaged F1 score computed for all labels except for O. sklearn-crfsuite.metrics package provides some useful metrics for sequence classification task, including this one.

In [326]:
#PERSON == 'B-PER' 'I-PER' (CONLL), ORG == 'B-ORG', GPE == 'B-LOC' 'I-LOC' (CONLL), MISC == TUDO QUE NAO AS OUTRAS 3 NO CONLL
labels = list(crf.classes_)
labels.remove('O')
labels


['B-MISC', 'B-PER', 'I-PER', 'B-LOC', 'B-ORG', 'I-ORG', 'I-MISC', 'I-LOC']

In [148]:
#Imprime o tamanho do y_test e y_pred e qtde de label predita
count = 0
for i,x in enumerate(y_pred):
        ss=set(x)
        if len(ss) > 1:
            count+=1
print("Qtde labels preditos", count)
print("tamanho em sentencas y_test", len(y_test))
print("tamanho em sentencas y_pred", len(y_pred))
print('tamanho em linhas y_test  ==>', len(sentences_trat_label))
print('tamanho em linhas y_pred  ==>', len(texto_sem_label_1))

Qtde labels preditos 1134
tamanho em sentencas y_test 25067
tamanho em sentencas y_pred 25067
tamanho em linhas y_test  ==> 517590
tamanho em linhas y_pred  ==> 517590


In [327]:
metrics.flat_f1_score(y_test, y_pred, 
                      average='weighted', labels=labels)

0.1442930895790253

Inspect per-class results in more detail:

In [328]:
# group B and I results
sorted_labels = sorted(
    labels,
    key=lambda name: (name[1:], name[0])
)
sorted_labels

['B-LOC', 'I-LOC', 'B-MISC', 'I-MISC', 'B-ORG', 'I-ORG', 'B-PER', 'I-PER']

In [329]:
print(metrics.flat_classification_report(
    y_test, y_pred, labels=sorted_labels, digits=3
))

              precision    recall  f1-score   support

       B-LOC      0.809     0.351     0.489      6312
       I-LOC      1.000     0.001     0.001      1854
      B-MISC      0.783     0.088     0.158      4029
      I-MISC      0.000     0.000     0.000      2781
       B-ORG      0.241     0.021     0.039      5574
       I-ORG      0.830     0.016     0.032      7499
       B-PER      0.842     0.099     0.176      6433
       I-PER      0.527     0.011     0.021      2753

   micro avg      0.749     0.093     0.166     37235
   macro avg      0.629     0.073     0.114     37235
weighted avg      0.659     0.093     0.144     37235



Hyperparameter Optimization

To improve quality try to select regularization parameters using randomized search and 3-fold cross-validation.

I takes quite a lot of CPU time and RAM (we’re fitting a model 50 * 3 = 150 times), so grab a tea and be patient, or reduce n_iter in RandomizedSearchCV, or fit model only on a subset of training data.



In [330]:
%%time
# define fixed parameters and parameters to search
crf = sklearn_crfsuite.CRF(
    algorithm='lbfgs',
    max_iterations=100,
    all_possible_transitions=True
)
params_space = {
    'c1': scipy.stats.expon(scale=0.5),
    'c2': scipy.stats.expon(scale=0.05),
}

# use the same metric for evaluation
f1_scorer = make_scorer(metrics.flat_f1_score,
                        average='weighted', labels=labels)

# search
rs = RandomizedSearchCV(crf, params_space,
                        cv=3,
                        verbose=1,
                        n_jobs=-1,
                        n_iter=50,
                        scoring=f1_scorer)
rs.fit(X_train, y_train)

Fitting 3 folds for each of 50 candidates, totalling 150 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 4 concurrent workers.
/Users/lucelia/anaconda3/envs/pos/lib/python3.9/site-packages/sklearn/base.py:209: FutureWarning: From version 0.24, get_params will raise an AttributeError if a parameter cannot be retrieved as an instance attribute. Previously it would return None.
  warnings.warn('From version 0.24, get_params will raise an '
/Users/lucelia/anaconda3/envs/pos/lib/python3.9/site-packages/sklearn/base.py:209: FutureWarning: From version 0.24, get_params will raise an AttributeError if a parameter cannot be retrieved as an instance attribute. Previously it would return None.
  warnings.warn('From version 0.24, get_params will raise an '
/Users/lucelia/anaconda3/envs/pos/lib/python3.9/site-packages/sklearn/base.py:209: FutureWarning: From version 0.24, get_params will raise an AttributeError if a parameter cannot be retrieved as an instance attribute. Previously it would return None.
  warnings.warn('From version 0.24, get_param

CPU times: user 2min 14s, sys: 9.1 s, total: 2min 23s
Wall time: 28min 40s


RandomizedSearchCV(cv=3,
                   estimator=CRF(algorithm='lbfgs',
                                 all_possible_transitions=True,
                                 keep_tempfiles=None, max_iterations=100),
                   n_iter=50, n_jobs=-1,
                   param_distributions={'c1': <scipy.stats._distn_infrastructure.rv_frozen object at 0x7fbfa3e7c370>,
                                        'c2': <scipy.stats._distn_infrastructure.rv_frozen object at 0x7fbf9b6dcac0>},
                   scoring=make_scorer(flat_f1_score, average=weighted, labels=['B-MISC', 'B-PER', 'I-PER', 'B-LOC', 'B-ORG', 'I-ORG', 'I-MISC', 'I-LOC']),
                   verbose=1)

Best result:

In [331]:
# crf = rs.best_estimator_
print('best params:', rs.best_params_)
print('best CV score:', rs.best_score_)
print('model size: {:0.2f}M'.format(rs.best_estimator_.size_ / 1000000))

best params: {'c1': 0.01591725484627282, 'c2': 0.07664136641928493}
best CV score: 0.8495779565846134
model size: 2.31M


In [ ]:
Check parameter space

A chart which shows which c1 and c2 values have RandomizedSearchCV checked. Red color means better results, blue means worse.

In [190]:
_x = [s.parameters['c1'] for s in rs.grid_scores_]
_y = [s.parameters['c2'] for s in rs.grid_scores_]
_c = [s.mean_validation_score for s in rs.grid_scores_]

fig = plt.figure()
fig.set_size_inches(12, 12)
ax = plt.gca()
ax.set_yscale('log')
ax.set_xscale('log')
ax.set_xlabel('C1')
ax.set_ylabel('C2')
ax.set_title("Randomized Hyperparameter Search CV Results (min={:0.3}, max={:0.3})".format(
    min(_c), max(_c)))

ax.scatter(_x, _y, c=_c, s=60, alpha=0.9, edgecolors=[0,0,0])

print("Dark blue => {:0.4}, dark red => {:0.4}".format(min(_c), max(_c)))

AttributeError: 'RandomizedSearchCV' object has no attribute 'grid_scores_'

Check best estimator on our test data

As you can see, quality is improved.

In [332]:
crf = rs.best_estimator_
y_pred = crf.predict(X_test)
print(metrics.flat_classification_report(
    y_test, y_pred, labels=sorted_labels, digits=3
))


              precision    recall  f1-score   support

       B-LOC      0.791     0.389     0.522      6312
       I-LOC      0.500     0.001     0.001      1854
      B-MISC      0.761     0.175     0.285      4029
      I-MISC      0.500     0.000     0.001      2781
       B-ORG      0.317     0.022     0.041      5574
       I-ORG      0.774     0.005     0.011      7499
       B-PER      0.821     0.117     0.204      6433
       I-PER      0.611     0.012     0.024      2753

   micro avg      0.755     0.110     0.193     37235
   macro avg      0.634     0.090     0.136     37235
weighted avg      0.669     0.110     0.165     37235



Let’s check what classifier learned

In [ ]:
#Let’s check what classifier learned
from collections import Counter

def print_transitions(trans_features):
    for (label_from, label_to), weight in trans_features:
        print("%-6s -> %-7s %0.6f" % (label_from, label_to, weight))

print("Top likely transitions:")
print_transitions(Counter(crf.transition_features_).most_common(20))

print("\nTop unlikely transitions:")
print_transitions(Counter(crf.transition_features_).most_common()[-20:])

We can see that, for example, it is very likely that the beginning of an organization name (B-ORG) will be followed by a token inside organization name (I-ORG), but transitions to I-ORG from tokens with other labels are penalized.

Check the state features:



In [ ]:
def print_state_features(state_features):
    for (attr, label), weight in state_features:
        print("%0.6f %-8s %s" % (weight, label, attr))

print("Top positive:")
print_state_features(Counter(crf.state_features_).most_common(30))

print("\nTop negative:")
print_state_features(Counter(crf.state_features_).most_common()[-30:])